# "Translation Word/Char Count Prediction (Part 3a)"

> Languages AFR, BEM, CHN, FAS
- toc: true
- branch: master
- badges: false
- comments: true
- hide: false
- search_exclude: true
- metadata_key1: metadata_value1
- metadata_key2: metadata_value2
- image: images/PredictTranslationWordAndCharCount_3.png
- categories: [Translation_Industry,  Regression,  Python,pandas,plotly]
- show_tags: true

In [ ]:
#hide
from google.colab import drive
drive.mount('/content/gdrive', force_remount=True)
root_dir = "/content/gdrive/My Drive/"
base_dir = root_dir + 'TODANALYTICS/'
# base_dir = ""

Mounted at /content/gdrive


## Purpose
There is a relationship between the number of words (and the number of characters) in the source language and the target language. If this relationship can be established and captured in yet another model, such a model can be helpful in at least two ways:

* For training: Validate the alignment of two sentences (in a training example) by comparing their *word size* and/or *character size*
* For inference: Validate the *word size* and/or *character size* of a translated/proofread sentence

In this notebook we will make good on our proposed value proposition to discover a model for each language and to evaluate its use in the above roles.

## Dataset and Variables

The dataset used in this notebook contains the following features:

* m_descriptor: Unique identifier of a document
* t_lan_E: Language of the translation (English is also considered a translation)
* t_version: Version of a translation
* s_rsen: Number of a sentence within a document
* c_id: Database primary key of a contribution
* e_content_E: Text content of an English contribution
* chars_E: Number of characters in an English contribution
* words_E: Number of words in an English contribution
* t_lan_V: Language of the translation
* e_top: N/A
* be_top: N/A
* c_created_at: Creation time of a contribution
* c_kind: Kind of a contribution
* c_base: N/A
* a_role: N/A
* u_name: N/A
* e_content_V: Text content of a translated contribution
* chars_V: Number of characters in a translated contribution
* words_V: Number of words in a translated contribution

# Setup the Environment

In [ ]:
from pathlib import Path
import pandas as pd
import plotly.express as px
%matplotlib inline

In [ ]:
!python --version

Python 3.6.9


In [ ]:
# PATH='./'
PATH = Path(base_dir + './'); #PATH

# Get train/valid data

We now ingest all the data we prepared in part 1. Note that the content (e_content) for each contribution is not displayed as it often makes the presentation unwieldy.

In [ ]:
#hide
def display_all(df):
    with pd.option_context("display.max_rows", 1000, "display.max_columns", 1000): 
        display(df)

## Language AFR

In [ ]:
df = pd.read_csv(f'{PATH}/PredictTranslationWordAndCharCount/PredictTranslationWordAndCharCount_2-AFR-output.csv', sep='~')
# df.loc[:5, ~df.columns.isin(['e_content_E','u_name','e_content_V','e_top','be_top','c_created_at','count','c_kind','c_base','a_role'])]
df.loc[:5, df.columns.isin(['m_descriptor','t_lan_E','t_version','s_rsen','c_id','chars_E','words_E','t_lan_V','chars_V','words_V'])]

m_descriptor t_lan_E t_version  s_rsen  ...  words_E  t_lan_V  chars_V words_V
0   1958-0928z     ENG   14-0101       1  ...        4      AFR       17       4
1   1958-0928z     ENG   14-0101       2  ...       51      AFR      299      53
2   1958-0928z     ENG   14-0101       3  ...       20      AFR      120      21
3   1958-0928z     ENG   14-0101       4  ...       22      AFR      133      23
4   1958-0928z     ENG   14-0101       5  ...       34      AFR      169      34
5   1958-0928z     ENG   14-0101       6  ...       21      AFR      111      19

[6 rows x 10 columns]

In [ ]:
#hide
# df

### Characters

In [ ]:
fig = px.scatter(data_frame=df, x='chars_E', y='chars_V', color='t_lan_V', 
                 title='Translation Characters vs English Characters', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                #  trendline="ols", 
                #  trendline="lowess", 
                #  trendline_color_override='black',
                 )
fig.show()

In [ ]:
#
#outlier
pd.set_option('display.max_colwidth',20)
outdf = df[(df['m_descriptor']=='CAB-05') & (df['s_rsen']==400)]
outdf

m_descriptor t_lan_E t_version  ...          e_content_V  chars_V words_V
70153       CAB-05     ENG   18-1101  ...  *Die wet van voo...      271      46

[1 rows x 20 columns]

In [ ]:
pd.set_option('display.max_colwidth',1000)
print(outdf.loc[:,['e_content_E']].values[0][0])
print(outdf.loc[:,['e_content_V']].values[0][0])

*The law of reproduction is that each specie brings forth after its own kind, even according to Genesis 1:11, ”And God said, Let the earth bring forth grass, and the herb yielding seed, and the fruit tree yielding fruit after his kind, whose seed is in itself, upon the earth: and it was so.“ Whatever life was in the seed came forth into a plant and thence into fruit.*
*Die wet van voortplanting is dat elke spesie voortbring volgens sy eie soort, selfs volgens Génesis 1: 11, "En God het gesê: Laat die aarde voortbring grasspruitjies, plante wat saad gee en bome wat, volgens hulle soorte, vrugte dra, waarin hulle saad is, op die aarde.*


Sure enough, this sentence is 'under-translated' and misses the last part in the English source sentence. We will remove this data-point and consider it an outlier.

In [ ]:
df = df.drop(70153)

In [ ]:
#
#outlier
pd.set_option('display.max_colwidth',20)
outdf = df[(df['m_descriptor']=='1965-0822x') & (df['s_rsen']==899)]
outdf

m_descriptor t_lan_E t_version  ...          e_content_V  chars_V words_V
54210   1965-0822x     ENG   18-0101  ...  *Die hele Skrif ...      132      21

[1 rows x 20 columns]

In [ ]:
pd.set_option('display.max_colwidth',1000)
print(outdf.loc[:,['e_content_E']].values[0][0])
print(outdf.loc[:,['e_content_V']].values[0][0])

*All scripture* (yeah) is *given by inspiration of* (Prophets? No.) … *inspiration of* (What?) *God, and is profitable for doctrine*, and *reproof*, and *correction*, and *instruction in righteousness:*
*Die hele Skrif is deur God ingegee en is nuttig tot lering, tot weerlegging, tot teregwysing, tot onderwysing in die geregtigheid*,


The translation lacks the injections in parentheses on the English side. Will be considered an outlier.


In [ ]:
df = df.drop(54210)

In [ ]:
#
#outlier
pd.set_option('display.max_colwidth',20)
outdf = df[(df['m_descriptor']=='1964-0418z') & (df['s_rsen']==178)]
outdf

m_descriptor t_lan_E t_version  ...          e_content_V  chars_V words_V
26290   1964-0418z     ENG   15-0402  ...  *Toe die Fariseë...      179      37

[1 rows x 20 columns]

In [ ]:
pd.set_option('display.max_colwidth',1000)
print(outdf.loc[:,['e_content_E']].values[0][0])
print(outdf.loc[:,['e_content_V']].values[0][0])

*Now when the Pharisee which had bidden him saw it, he spake within himself*, (remember, not out loud), *within himself, saying*, If this man … was *a prophet*, he would *know who and what manner of woman this is that* touched *him … for she is a sinner*.
*Toe die Fariseër wat Hom genooi het, dit sien, sê hy by homself: Hy as Hy 'n profeet was, sou geweet het wie en watter soort vrou dit is wat Hom aanraak; want sy is 'n sondares.*


Again, the translation lacks the injection in parentheses on the English side. Will be considered an outlier.

In [ ]:
df = df.drop(26290)

In [ ]:
#hide
fig = px.scatter(data_frame=df, x='chars_E', y='chars_V', color='t_lan_V', 
                 title='Translation Characters vs English Characters', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                 trendline="ols", 
                 trendline_color_override='black',)
fig.show()
results = px.get_trendline_results(fig)
results.px_fit_results.iloc[0].summary()

### Words

In [ ]:
fig = px.scatter(data_frame=df, x='words_E', y='words_V', color='t_lan_V', 
                 title='Translation Words vs English Words', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                 )
fig.show()

In [ ]:
#hide
fig = px.scatter(data_frame=df, x='words_E', y='words_V', color='t_lan_V', 
                 title='Translation Words vs English Words', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                 trendline="ols", 
                 trendline_color_override='black')
fig.show()
results = px.get_trendline_results(fig)
results.px_fit_results.iloc[0].summary()

In [ ]:
df.to_csv (f'{PATH}/PredictTranslationWordAndCharCount/PredictTranslationWordAndCharCount_3-AFR-output.csv', sep='~', index = False, header=True)

## Language BEM

In [ ]:
df = pd.read_csv(f'{PATH}/PredictTranslationWordAndCharCount/PredictTranslationWordAndCharCount_2-BEM-output.csv', sep='~')
df.loc[:5, df.columns.isin(['m_descriptor','t_lan_E','t_version','s_rsen','c_id','chars_E','words_E','t_lan_V','chars_V','words_V'])]

m_descriptor t_lan_E t_version  s_rsen  ...  words_E  t_lan_V  chars_V words_V
0    1955-0121     ENG   15-0401       1  ...        4      BEM       24       3
1    1955-0121     ENG   15-0401       2  ...        4      BEM       27       4
2    1955-0121     ENG   15-0401       3  ...        6      BEM       38       5
3    1955-0121     ENG   15-0401       4  ...       10      BEM       46       8
4    1955-0121     ENG   15-0401       5  ...       37      BEM      213      34
5    1955-0121     ENG   15-0401       6  ...       29      BEM      167      27

[6 rows x 10 columns]

In [ ]:
#hide
# df

### Characters

In [ ]:
fig = px.scatter(data_frame=df, x='chars_E', y='chars_V', color='t_lan_V', 
                 title='Translation Characters vs English Characters', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                 )
fig.show()

In [ ]:
#
#outlier
pd.set_option('display.max_colwidth',20)
outdf = df[(df['m_descriptor']=='1965-0822x') & (df['s_rsen']==1)]
outdf

m_descriptor t_lan_E t_version  ...          e_content_V  chars_V words_V
24010   1965-0822x     ENG   18-0101  ...  Natukontamike im...      273      41

[1 rows x 20 columns]

In [ ]:
pd.set_option('display.max_colwidth',1000)
print(outdf.loc[:,['e_content_E']].values[0][0])
print(outdf.loc[:,['e_content_V']].values[0][0])

Let us bow our heads.
Natukontamike imitwe yesu. Shikulu Yesu, ka Cema wa mukuni mukalamba,Ifye natukwata imisha ishingi kuli Imwe,Shikulu, isho ifwe ta twa katale lipila pa citemwiko ico mwabika mu mitima Yesu. Ifwe tuleufwa abashalinga ilyo tunkontamike imitwe yesu no kwiminina mumulola Wenu.


This data-point is definitely an outlier.

In [ ]:
df = df.drop(24010)

In [ ]:
#hide
fig = px.scatter(data_frame=df, x='chars_E', y='chars_V', color='t_lan_V', 
                 title='Translation Characters vs English Characters', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                 trendline="ols", trendline_color_override='black')
fig.show()
results = px.get_trendline_results(fig)
results.px_fit_results.iloc[0].summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.968
Model:                            OLS   Adj. R-squared:                  0.968
Method:                 Least Squares   F-statistic:                 9.103e+05
Date:                Thu, 22 Oct 2020   Prob (F-statistic):               0.00
Time:                        03:20:20   Log-Likelihood:            -1.1022e+05
No. Observations:               29791   AIC:                         2.204e+05
Df Residuals:                   29789   BIC:                         2.205e+05
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const          1.8522      0.089     20.807      0.000       1.678       2.027
x1             1.1190      0.001    954.114      0.000       1.117       1.121
==============================================================================
Omnibus:                     3665.975   Durbin-Watson:                   2.015
Prob(Omnibus):                  0.000   Jarque-Bera (JB):            41651.082
Skew:                          -0.061   Prob(JB):                         0.00
Kurtosis:                       8.791   Cond. No.                         119.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

### Words

In [ ]:
fig = px.scatter(data_frame=df, x='words_E', y='words_V', color='t_lan_V', 
                 title='Translation Words vs English Words', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                )
fig.show()

In [ ]:
#hide
fig = px.scatter(data_frame=df, x='words_E', y='words_V', color='t_lan_V', 
                 title='Translation Words vs English Words', 
                 opacity=.5, 
                 hover_data=['m_descriptor','t_lan_V','s_rsen'], 
                 labels={'m_descriptor':'Descriptor','t_lan_V':'','s_rsen':'Sentence No'},
                 trendline="ols", 
                 trendline_color_override='black')
fig.show()
results = px.get_trendline_results(fig)
results.px_fit_results.iloc[0].summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.951
Model:                            OLS   Adj. R-squared:                  0.951
Method:                 Least Squares   F-statistic:                 5.796e+05
Date:                Thu, 22 Oct 2020   Prob (F-statistic):               0.00
Time:                        03:20:31   Log-Likelihood:                -60456.
No. Observations:               29791   AIC:                         1.209e+05
Df Residuals:                   29789   BIC:                         1.209e+05
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.0277      0.017     -1.621      0.105      -0.061       0.006
x1             0.8686      0.001    761.290      0.000       0.866       0.871
==============================================================================
Omnibus:                     2966.283   Durbin-Watson:                   1.998
Prob(Omnibus):                  0.000   Jarque-Bera (JB):            18122.307
Skew:                           0.278   Prob(JB):                         0.00
Kurtosis:                       6.780   Cond. No.                         24.0
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [ ]:
df.to_csv (f'{PATH}/PredictTranslationWordAndCharCount/PredictTranslationWordAndCharCount_3-BEM-output.csv', sep='~', index = False, header=True)